In [0]:
# =============================================================================
# 📊 PIPELINE ETL - Offres d'Emploi IA/ML France
# =============================================================================

# Charger le fichier CSV depuis le Volume
df = spark.read.format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load("/Volumes/workspace/default/data_emploi/offres_ia_france_20260212_144803.csv")

# Afficher les premières lignes
display(df)

id titre entreprise type_contrat type_contrat_libelle experience salaire ville code_postal departement region competences nombre_competences date_creation date_actualisation description url secteur_activite qualification mot_cle_recherche 203RZPZ Spécialiste IA / Machine Learning Engineer (H/F) R(E) GREEN CDI CDI 48 Mois Annuel de 50000.0 Euros à 55000.0 Euros sur 12.0 mois 75 - PARIS 09 75009 75 Île-de-France Développer des modèles prédictifs pour l'analyse de données, Documenter les processus et les architectures d'IA, Optimiser les performances des systèmes d'IA 3 2026-02-06 10:30:38.425000+00:00 2026-02-06 10:30:38.425000+00:00 Spécialiste IA / Machine Learning Engineer
 null null null null Développement d'API IA & entraînement de modèles propriétaires null null null null null null null null null null null null null null null null null null null Gecob.tech null null null null null null null null null null null null null null null null null null null France / Remote possible null null null null null null null null null null null null null null null null null null null CDI ou Freelance longue durée null null null null null null null null null null null null null null null null null null null Contexte null null null null null null null null null null null null null null null null null null null Gecob.tech est une plateforme SaaS et DeepTech dédiée à l'immobilier à la data et à la décarbonation avec une forte ambition technologique : null null null null null null null null null null null null null null null null null développer et entraîner des modèles d'IA propriétaires null null null null null null null null null null null null null null null null null null null connecter intelligemment des API externes null null null null null null null null null null null null null null null null null null null industrialiser des traitements IA à forte valeur métier. null null null null null null null null null null null null null null null null null null null Dans ce ca" https://candidat.francetravail.fr/offres/recherche/detail/203RZPZ Autres activités auxiliaires de services financiers, hors assurance et caisses de retraite, n.c.a. Agent de maîtrise Machine Learning null null null null null null null null null null null null null null null 202TGLX Ingénieur en Machine Learning Senior (H/F) CELIOS TECHNOLOGIES CDI CDI 5 An(s) Annuel de 70000.0 Euros à 85000.0 Euros sur 12.0 mois 92 - Suresnes 92150 92 Île-de-France null 0 2026-01-16 18:06:25.531000+00:00 2026-02-01 21:45:22.544000+00:00 Notre client : 
 null null null null Une entreprise qui développe des solutions logicielles de pointe en intelligence artificielle et en traitement de données massives. Elle accompagne les organisations publiques et privées dans l'exploitation de leurs données pour améliorer la prise de décision la sécurité et la performance opérationnelle. null null null null null null null null null null null null null null null null null null Mission : null null null null null null null null null null null null null null null null null null null Au sein des équipes R&D le ML Engineer est un expert technique qui conçoit développe et déploie des systèmes d'intelligence artificielle dans des environnements com" https://candidat.francetravail.fr/offres/recherche/detail/202TGLX Conseil en systèmes et logiciels informatiques Cadre Machine Learning null null null null null null null null null null null null null null 203KZVV Ingénieur ou Ingénieure de recherche en intelligence artificielle (H/F) SCES COMMUNS IMT BUSINESS SCHOOL TELECOM CDD CDD - 10 Mois 2 An(s) Annuel de 33500.0 Euros à 36000.0 Euros sur 12.0 mois 91 - EVRY 91000 91 Île-de-France Connaissance des normes de sécurité des données en santé, Connaissance des standards internationaux de santé numérique, Evaluation des technologies de santé, Communiquer avec les professionnels de santé pour collecter des informations, Concevoir des solutions numériques adaptées au secteur de la santé, Gérer des projets de développeme

In [0]:
# Afficher le schéma des données
print("📋 SCHÉMA DES DONNÉES:")
df.printSchema()

# Compter le nombre de lignes
nb_lignes = df.count()
print(f"\n📊 NOMBRE TOTAL D'OFFRES: {nb_lignes}")

📋 SCHÉMA DES DONNÉES:
root
 |-- id: string (nullable = true)
 |-- titre: string (nullable = true)
 |-- entreprise: string (nullable = true)
 |-- type_contrat: string (nullable = true)
 |-- type_contrat_libelle: string (nullable = true)
 |-- experience: string (nullable = true)
 |-- salaire: string (nullable = true)
 |-- ville: string (nullable = true)
 |-- code_postal: string (nullable = true)
 |-- departement: string (nullable = true)
 |-- region: string (nullable = true)
 |-- competences: string (nullable = true)
 |-- nombre_competences: string (nullable = true)
 |-- date_creation: string (nullable = true)
 |-- date_actualisation: string (nullable = true)
 |-- description: string (nullable = true)
 |-- url: string (nullable = true)
 |-- secteur_activite: string (nullable = true)
 |-- qualification: string (nullable = true)
 |-- mot_cle_recherche: string (nullable = true)


📊 NOMBRE TOTAL D'OFFRES: 6229


In [0]:
from pyspark.sql.functions import col, when, trim, lower, count, desc

# =============================================================================
# 🧹 NETTOYAGE DES DONNÉES
# =============================================================================

# 1. Supprimer les doublons
df_clean = df.dropDuplicates(["id"])

# 2. Nettoyer les valeurs nulles et "Non précisé"
df_clean = df_clean.withColumn(
    "region", 
    when(col("region").isNull() | (col("region") == ""), "Non précisé")
    .otherwise(col("region"))
)

df_clean = df_clean.withColumn(
    "entreprise",
    when(col("entreprise").isNull() | (col("entreprise") == ""), "Non précisé")
    .otherwise(col("entreprise"))
)

# 3. Nettoyer les espaces
df_clean = df_clean.withColumn("titre", trim(col("titre")))
df_clean = df_clean.withColumn("region", trim(col("region")))

# Afficher les stats
print(f"📊 Avant nettoyage: {df.count()} lignes")
print(f"✅ Après nettoyage: {df_clean.count()} lignes")
print(f"🗑️  Doublons supprimés: {df.count() - df_clean.count()}")

📊 Avant nettoyage: 6229 lignes
✅ Après nettoyage: 5096 lignes
🗑️  Doublons supprimés: 1133


In [0]:
print("🗺️ TOP 10 RÉGIONS:")
df_regions = df_clean.groupBy("region").count().orderBy(desc("count"))
display(df_regions)

🗺️ TOP 10 RÉGIONS:


region count Non précisé 3636 Île-de-France 447 Occitanie 185 Auvergne-Rhône-Alpes 151 PACA 123 Nouvelle-Aquitaine 100 Pays de la Loire 99 Bretagne 92 Hauts-de-France 80 Grand Est 58 Centre-Val de Loire 28 Normandie 24 Bourgogne-Franche-Comté 24 DOM-TOM 13 Intelligence Artificielle 9 Machine Learning 4 Data Engineer 3 0 2 Data Scientist 2 Corse 2 Cadre 2 cybersécurité Historiquement implantés en région parisienne 1 co" 1 Depuis plus de 30 ans, CENTUM T&S apporte conseil et expertise à ses clients dans le domaine de l'électronique embarquée. Nous offrons une large gamme de services d'ingénierie de conception de systèmes électroniques embarqués aux clients mondiaux pour les aider à réaliser des produits et des sous-systèmes complexes. Centum T&S est un centre d'excellence en conception électronique, concevant pour des projets critiques dans les domaines de l'aérospatiale/aéronautique, des transports, de l'électron 1 vous : 1 Big Data & IA. 1 Azure 1 Big data 1 Traitement de données, hébergement et activités connexes 1 https://candidat.francetravail.fr/offres/recherche/detail/8949980 1 fabricants d'acier et d'équipements et entreprises de trait" 1 offrant un environnement de travail mod" 1 https://candidat.francetravail.fr/offres/recherche/detail/8462273 1

In [0]:
# 2. Offres par type de contrat
print("📝 RÉPARTITION PAR TYPE DE CONTRAT:")
df_contrats = df_clean.groupBy("type_contrat_libelle").count().orderBy(desc("count"))
display(df_contrats)

📝 RÉPARTITION PAR TYPE DE CONTRAT:


type_contrat_libelle count null 2444 CDI 1362 Intelligence Artificielle 334 Machine Learning 90 Data Engineer 90 Intérim - 1 Mois 84 CDD - 12 Mois 80 Cadre 57 CDD - 36 Mois 44 Data Scientist 26 Profession libérale 18 CDD - 6 Mois 15 Intérim - 18 Mois 15 Intérim - 3 Mois 13 Employé qualifié 13 Technicien 11 Agent de maîtrise 8 Conseil pour les affaires et autres conseils de gestion 7 Intérim - 6 Mois 6 CDD - 4 Mois 5 Conseil en systèmes et logiciels informatiques 5 CDD - 24 Mois 5 Intérim - 2 Mois 5 Activités des agences de travail temporaire 5 Édition de logiciels applicatifs 4 Intérim - 8 Mois 3 Ingénierie,études techniques 3 CDD - 18 Mois 3 CDD - 9 Mois 3 Activités des agences de placement de main-d'œuvre 3 CDD - 10 Mois 3 Profession libérale - 2 Jour(s) 3 CDD - 3 Mois 2 Commerce d'alimentation générale 2 du jeune diplômé au cadre exécutif. Nous collaborons avec des entreprises de référence 2 et nos experts sont là pour l'analyser 2 Profession libérale - 12 Mois 2 CDD - 8 Mois 2 Intérim - 12 Mois 2 tes points de suivi tout au long de tes missions et tes Entretiens Annuels. 2 avec le souci du détail et de la qualité. 2 https://candidat.francetravail.fr/offres/recherche/detail/8368745 1 de l'Industrie et des Servi" 1 métallurgiques 1 industrie 1 https://candidat.francetravail.fr/offres/recherche/detail/7223759 1 https://candidat.francetravail.fr/offres/recherche/detail/202XQGZ 1 Lyon 1 Fabrication d'éléments en matières plastiques pour la construction 1 Fabrication de produits pharmaceutiques de base 1 .) 1 Python 1 https://candidat.francetravail.fr/offres/recherche/detail/203FQSG 1 https://candidat.francetravail.fr/offres/recherche/detail/202WLBF 1 Annuel de 50000.0 Euros à 60000.0 Euros 1 où de nouvelles Business Units se développent et où de nouveaux leviers de croissance sont recherchés 1 du digital 1 innovantes et sécurisées pour répondre aux besoins et aux attentes des clients et des collaborateurs 1 Action sociale sans hébergement n.c.a. 1 si toutefois vous l'acceptez 1 nous innovons chaque jour au service de performances industrielles durab" 1 énergie et haute technologie. 1 nous disposons d'expertises sectorielles de premier plan et d'un portefeuil" 1 JAVA 1 l'Agroalimentaire 1 noyau/RTOS 1 le QMS MasterControl 1 pour des clients issus de secteurs industriels variés : agroalimentaire 1 Intérim - 5 Jour(s) 1 l'alert" 1 dans le respect sincère de la planète et de ses collaborateurs. 1 https://candidat.francetravail.fr/offres/recherche/detail/203DPLW 1 ferroviaire 1 sélectionne et négocie au mieux de leurs intérêts des solutions de crédit 1 https://candidat.francetravail.fr/offres/recherche/detail/203NWNP 1 Profession commerciale 1 Intérim - 89 Jour(s) 1 favorisant la collaboration 1 et des données de la déclaration sociale nominative. Pour chaque cohorte de sortants de toutes les formations du supérieur (universitaires 1 Make 1 production 1 CDD - 11 Mois 1 https://candidat.francetravail.fr/offres/recherche/detail/203WWHP 1 heatmaps. 1 Rédiger un cahier des charges 1 de solutions informatiques de gestion destinées au marché du pneumatique et de la pièce détachée automobile. 1 expertise comptable 1 https://candidat.francetravail.fr/offres/recherche/detail/8734626 1 partager 1 chariots élévateurs.) et multilocation (piqueurs 1 etc Vos principales responsabilités Exploiter et analyser des données internes et externes afin d'éclairer la prise de décision. 1 https://candidat.francetravail.fr/offres/recherche/detail/9006201 1 Commerce de gros (commerce interentreprises) d'ordinateurs, d'équipements informatiques périphériques et de logiciels 1 https://candidat.francetravail.fr/offres/recherche/detail/8122536 1 etc.) 1 Formation continue d'adultes 1 automobile 1 https://candidat.francetravail.fr/offres/recherche/detail/202PZHN 1 https://candidat.francetravail.fr/offres/recherche/detail/8756740 1 conçoit depuis 2019 des solutions sur mesure en machine learning 1 mécanismes de détection et de réponse aux incidents. 1 SSI 1 la DSN

In [0]:
# =============================================================================
# 💾 SAUVEGARDE EN DELTA LAKE
# =============================================================================

# 1. Sauvegarder la table principale nettoyée
df_clean.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.default.offres_emploi_ia")

print("✅ Table 'offres_emploi_ia' sauvegardée en Delta Lake!")

# 2. Sauvegarder l'agrégation par région
df_regions.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.default.offres_par_region")

print("✅ Table 'offres_par_region' sauvegardée!")

# 3. Sauvegarder l'agrégation par contrat
df_contrats.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.default.offres_par_contrat")

print("✅ Table 'offres_par_contrat' sauvegardée!")

print("\n🎉 PIPELINE ETL TERMINÉ!")

✅ Table 'offres_emploi_ia' sauvegardée en Delta Lake!
✅ Table 'offres_par_region' sauvegardée!
✅ Table 'offres_par_contrat' sauvegardée!

🎉 PIPELINE ETL TERMINÉ!
